In [1]:
import pandas as pd
from matplotlib import pyplot as plt
import numpy as np
from wordcloud import WordCloud

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold, StratifiedShuffleSplit
from sklearn.metrics import confusion_matrix
from sklearn.metrics import ConfusionMatrixDisplay

import re
import string
from stop_words import get_stop_words

from imblearn.over_sampling import RandomOverSampler

import spacy

from nltk import ngrams



In [2]:
pd.set_option("display.max_colwidth", 255)
pd.set_option('display.max_rows', 255)

In [3]:
df = pd.read_excel("training-nltk-mapping3.xlsx")
cnt = df.groupby("CASISTICA_MOTIVAZIONE").count() \
.rename(columns={"Unnamed: 0": "count"})["count"]

In [ ]:
def prune_infrequent_classes(input_df: pd.DataFrame):
    card_thresh = 10
    cnt = input_df[["CASISTICA_MOTIVAZIONE","NOTE_OPERATORE"]].groupby(["CASISTICA_MOTIVAZIONE"]).count().rename({"NOTE_OPERATORE":"count"},axis=1)
    res = input_df.merge(cnt, on="CASISTICA_MOTIVAZIONE")
    res = res[res["count"] >= card_thresh]
    res = res.drop("count", axis=1)
    return res


In [11]:
def unique_str(l:list[str]):
    return list(set(l))

def apply_ngram(l:list[str], n:int):
    return list(ngrams(l, n))

def join_string_list(l:list[tuple[str]]):
    return [" ".join(list(i)) for i in l]

In [ ]:
def get_unique_ngrams(df: pd.DataFrame, n:int):
    df_cp = df[["CASISTICA_LAVORAZIONE","NOTE_OPERATORE","CASISTICA_MOTIVAZIONE"]]

    #make all strings lowercase
    df_cp["NOTE_OPERATORE_lower"] = df_cp["NOTE_OPERATORE"].str.lower()

    #make column as a list of words (1-gram)
    splitted_col_name = "NOTE_OPERATORE_split_{}gram".format(str(n))
    df_cp["NOTE_OPERATORE_split_1gram"] = df_cp["NOTE_OPERATORE_lower"].str.split(" ")

    #if n!=1 make a column as a list of n-grams
    if(n!=1):
        df_cp[splitted_col_name] = df_cp["NOTE_OPERATORE_split_1gram"].apply(lambda x: apply_ngram(x, n))

    ngram_col_name = "NOTE_OPERATORE_{}gram_unique_words".format(str(n))

    #make sure every n-gram in every row is not repeated
    df_cp[ngram_col_name] = df_cp[splitted_col_name].apply(lambda x: unique_str(x))

    #concat every word composing a n-gram, transforming the column from a list[tuple[str]] to list[str]
    if(n!=1):
        df_cp[ngram_col_name] = df_cp[ngram_col_name].apply(lambda x: join_string_list(x))


    #explode the df, to make a row for every n-gram - then groupBy [class, n-gram] to find how many records contain every n-gram
    df_cp_ngram = df_cp[[ngram_col_name, "CASISTICA_MOTIVAZIONE", "CASISTICA_LAVORAZIONE"]].explode(ngram_col_name) \
        .groupby(["CASISTICA_MOTIVAZIONE",ngram_col_name]).count()\
        .sort_values(by=["CASISTICA_MOTIVAZIONE", "CASISTICA_LAVORAZIONE"], ascending=[True,False])\
        .reset_index() \
        .rename(columns={"CASISTICA_LAVORAZIONE":"count"})


    #self-join the df to find every n-gram occurring in just one class
    df_cp_ngram_mrg = df_cp_ngram.merge(df_cp_ngram, how="left", on=ngram_col_name)
    df_cp_ngram_mrg = df_cp_ngram_mrg.rename(columns={"count_x":"ngram_occurrencies"})

    df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE = df_cp_ngram_mrg.groupby(["CASISTICA_MOTIVAZIONE_x", ngram_col_name]).count()
    
    df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE = df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE.reset_index()
    df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE = df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE[["CASISTICA_MOTIVAZIONE_x", ngram_col_name, "count_y"]] \
        .rename(columns={"count_y":"ngram_occurrencies_in_CASISTICA_MOTIVAZIONE", "CASISTICA_MOTIVAZIONE_x": "CASISTICA_MOTIVAZIONE"})
    
    # find every n-gram occurring in just one class (it was groupedBy + count by [class,n-gram])
    df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE = df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE[df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE["ngram_occurrencies_in_CASISTICA_MOTIVAZIONE"] == 1]

    #merge the new DF to produce the final result
    res = df_cp_ngram_mrg.merge(df_cp_ngram_mrg_uniqueCASISTICAMOTIVAZIONE, on=ngram_col_name)

    res = res[["CASISTICA_MOTIVAZIONE_x", ngram_col_name, "ngram_occurrencies"]] #"ngram_occurrencies_in_CASISTICA_MOTIVAZIONE"
    res = res.rename(columns={"CASISTICA_MOTIVAZIONE_x":"CASISTICA_MOTIVAZIONE"})

    res = res.sort_values(by = "ngram_occurrencies", ascending=False)

    #groupBy and merge the original DF to create the column "record_per_class", indicating how many record occurr in every class
    df_grp_class = df.groupby("CASISTICA_MOTIVAZIONE").count().reset_index()
    df_grp_class = df_grp_class.rename(columns={"Unnamed: 0":"record_per_class"})
    df_grp_class = df_grp_class[["CASISTICA_MOTIVAZIONE", "record_per_class"]]

    res = res.merge(df_grp_class, on="CASISTICA_MOTIVAZIONE")

    return res


gram_dim = 2
res= get_unique_ngrams(df, gram_dim)

res.iloc[:25]


C:\Users\a.torchi\AppData\Local\Temp\ipykernel_31116\2333237563.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cp["NOTE_OPERATORE_lower"] = df_cp["NOTE_OPERATORE"].str.lower()


CASISTICA_MOTIVAZIONE NOTE_OPERATORE_2gram_unique_words  \
0        Periodo diverso                       allega vers   
1               Generica                 veicolo intestato   
2               Generica                        essere mai   
3        Periodo diverso                 periodi tributari   
4        Periodo diverso              scansiona versamento   
5     Furto non annotato                  furto trascritto   
6        Periodo diverso                    relativa vers.   
7        Periodo diverso                versamento periodo   
8        Periodo diverso                     relativa anno   
9               Generica                  dichiara vendita   
10              Generica                 intestato società   
11              Generica                modalità pagamento   
12              Generica                     scrive essere   
13       Periodo diverso                   diverso periodo   
14       Vendita tardiva                     lombardo mese   
15       Periodo diverso             successivo versamento   
16              Generica                 annotazione carta   
17              Generica              demolizione annotata   
18              Generica              dichiara demolizione   
19              Generica            documentazione carente   
20              Generica                       nessun atto   
21              Generica              risulta intestatario   
22              Generica               documento didentità   
23              Generica                           on line   
24       Vendita tardiva                      venduta dopo   

    ngram_occurrencies  record_per_class  
0                   28               831  
1                   15              2763  
2                   14              2763  
3                   14               831  
4                   14               831  
5                   12               116  
6                   12               831  
7                   12               831  
8                   11               831  
9                   10              2763  
10                  10              2763  
11                  10              2763  
12                  10              2763  
13                  10               831  
14                   9               257  
15                   9               831  
16                   9              2763  
17                   9              2763  
18                   9              2763  
19                   9              2763  
20                   9              2763  
21                   9              2763  
22                   8              2763  
23                   8              2763  
24                   8               257

In [ ]:
n=3
splitted_col_name = "NOTE_OPERATORE_split_{}gram".format(str(n))
df_cp=df.copy()

#concatenate every string within the same class
df_cp = df_cp.sort_values(by="CASISTICA_MOTIVAZIONE")
df_cp["cat"] = df_cp.groupby(['CASISTICA_MOTIVAZIONE'])['NOTE_OPERATORE'].transform(lambda x : ' '.join(x))
df_cp["cat"] = df_cp["cat"].str.lower()
df_cp = df_cp.groupby(["CASISTICA_MOTIVAZIONE", "cat"]).count().reset_index()

#make column as a list of words (1-gram), then create a column of n-grams
df_cp[splitted_col_name] = df_cp["cat"].str.split(" ").apply(lambda x: apply_ngram(x, n))

#count the occurrences for every n-gram for every class
df_cp["count_placeholder"] = 1
df_cp = df_cp[["CASISTICA_MOTIVAZIONE", splitted_col_name, "count_placeholder"]].explode(splitted_col_name)\
    .groupby(["CASISTICA_MOTIVAZIONE", splitted_col_name]).count() \
    .reset_index() \
    .sort_values(by="count_placeholder")

#self-join to find which classes (except the currently considerated one) have a given n-gram, for every n-gram and every class
df_cp_selfjoin = df_cp[["CASISTICA_MOTIVAZIONE", splitted_col_name, "count_placeholder"]].rename(columns={"CASISTICA_MOTIVAZIONE": "CASISTICA_MOTIVAZIONE_selfjoin", "count_placeholder":"count_selfjoin"})
df_cp = df_cp.merge(df_cp_selfjoin, on=splitted_col_name)
df_cp = df_cp[df_cp["CASISTICA_MOTIVAZIONE"] != df_cp["CASISTICA_MOTIVAZIONE_selfjoin"]]

# find how many occurrences of a given n-gram exist in every other class (except the currently considerated one), for every n-gram and every class
df_cp_tfidf = df_cp[["CASISTICA_MOTIVAZIONE", splitted_col_name, "count_selfjoin"]].groupby(["CASISTICA_MOTIVAZIONE", splitted_col_name]).sum("count_selfjoin") \
    .rename(columns={"count_selfjoin": "sum_selfjoin"})
df_cp = df_cp.merge(df_cp_tfidf, on=["CASISTICA_MOTIVAZIONE", splitted_col_name])

#for every n-gram and every class, divide the occurrences of that n-gram in that class by the sum of the occurrences of that n-gram in every other class
df_cp["tf_idf"] = df_cp["count_placeholder"] / df_cp["sum_selfjoin"]

df_cp = df_cp.sort_values(by="tf_idf")

df_cp.iloc[-115:]


CASISTICA_MOTIVAZIONE  \
2627                    Generica   
2626                    Generica   
2625             Periodo diverso   
2587          Furto non annotato   
2588          Furto non annotato   
2386             Periodo diverso   
2335             Regione diversa   
2347          Furto non annotato   
2356             Vendita tardiva   
2384             Periodo diverso   
2379             Vendita tardiva   
2345          Furto non annotato   
2302             Periodo diverso   
2340                    Generica   
2315             No esenzione PH   
2295             Periodo diverso   
2296                    Generica   
2317                    Generica   
2316  Esenzione PH senza istanza   
2336             Periodo diverso   
2355                    Generica   
2282                    Generica   
2280             Vendita tardiva   
2273                    Generica   
2277                    Generica   
2330             Regione diversa   
2383             Vendita tardiva   
2272             Periodo diverso   
2270                    Generica   
2309                    Generica   
2279                    Generica   
2304             Periodo diverso   
2645             Vendita tardiva   
2646             Vendita tardiva   
2607                    Generica   
2608                    Generica   
2463             Periodo diverso   
2616             Periodo diverso   
2615             Periodo diverso   
2467             Periodo diverso   
2462                    Generica   
2390             Vendita tardiva   
2612          Furto non annotato   
2395                    Generica   
2394             Periodo diverso   
2476             Periodo diverso   
2448                    Generica   
2446                    Generica   
2420  Esenzione PH senza istanza   
2611          Furto non annotato   
2662                    Generica   
2664                    Generica   
2665                    Generica   
2666                    Generica   
2663                    Generica   
2635             Periodo diverso   
2636             Periodo diverso   
2483                    Generica   
2639                    Generica   
2534             Periodo diverso   
2512             Periodo diverso   
2533                    Generica   
2518             Vendita tardiva   
2482             Periodo diverso   
2642             Periodo diverso   
2644             Periodo diverso   
2643             Periodo diverso   
2479             Periodo diverso   
2652                    Generica   
2651                    Generica   
2683             Periodo diverso   
2680             Periodo diverso   
2682             Periodo diverso   
2681             Periodo diverso   
2737             Vendita tardiva   
2740             Vendita tardiva   
2745             Vendita tardiva   
2744             Vendita tardiva   
2743             Vendita tardiva   
2739             Vendita tardiva   
2738             Vendita tardiva   
2742             Vendita tardiva   
2741             Vendita tardiva   
2654             Vendita tardiva   
2653             Vendita tardiva   
2579                    Generica   
2572             Periodo diverso   
2576             Periodo diverso   
2578             Periodo diverso   
2566             Periodo diverso   
2731             Vendita tardiva   
2733             Vendita tardiva   
2732             Vendita tardiva   
2735             Vendita tardiva   
2734             Vendita tardiva   
2736             Vendita tardiva   
2730             Vendita tardiva   
2591             Periodo diverso   
2589                       Fermo   
2583          Furto non annotato   
2586             Vendita tardiva   
2590                    Generica   
2602             Periodo diverso   
2610             Regione diversa   
2609                    Generica   
2614             Vendita tardiva   
2621             Periodo diverso   
2613             Vendita tardiva   
2620             Periodo diverso   
2637             Periodo diverso   
2624           